In [1]:
from pathlib import Path
import random 

from manipylator import HeadlessSimulatedRobot, SimulatedRobot
from manipylator.utils import render_robot_from_template

In [2]:
with render_robot_from_template("robots/empiric") as robot_urdf:
    manny = HeadlessSimulatedRobot(robot_urdf)
print(manny.model)

[I 07/27/25 00:29:05.580 2222] [shell.py:_shell_pop_print@23] Graphical python shell detected, using wrapped sys.stdout


[Genesis] [00:29:19] [INFO] ╭───────────────────────────────────────────────╮
[Genesis] [00:29:19] [INFO] │┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈ Genesis ┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈│
[Genesis] [00:29:19] [INFO] ╰───────────────────────────────────────────────╯
[Genesis] [00:29:19] [WARNING] No Intel XPU device available. Falling back to CPU for torch device.


/opt/conda/lib/python3.11/site-packages/torch/cuda/__init__.py:129: UserWarning: CUDA initialization: CUDA unknown error - this may be due to an incorrectly set up environment, e.g. changing env variable CUDA_VISIBLE_DEVICES after program start. Setting the available devices to be zero. (Triggered internally at ../c10/cuda/CUDAFunctions.cpp:108.)
  return torch._C._cuda_getDeviceCount() > 0


[Genesis] [00:29:21] [INFO] Consider setting 'performance_mode=True' in production to maximise runtime speed, if significantly increasing compilation time is not a concern.


RHI Error: Can not create Vulkan instance
[W 07/27/25 00:29:21.075 2222] [misc.py:adaptive_arch_select@758] Arch=[<Arch.vulkan: 10>] is not supported, falling back to CPU


[Genesis] [00:29:23] [INFO] Running on [Intel(R) Core(TM) i7-8665U CPU @ 1.90GHz] with backend gs.cpu. Device memory: 15.25 GB.
[Genesis] [00:29:23] [INFO] 🚀 Genesis initialized. 🔖 version: 0.2.1, 🌱 seed: None, 📏 precision: '32', 🐛 debug: False, 🎨 theme: 'dark'.
[Genesis] [00:29:23] [WARNING] Scene.show_FPS is deprecated. Please use Scene.profiling_options.show_FPS
[Genesis] [00:29:23] [INFO] Scene <4cb4c04> created.
[Genesis] [00:29:23] [INFO] Adding <gs.RigidEntity>. idx: 0, uid: <26f5114>, morph: <gs.morphs.Plane>, material: <gs.materials.Rigid>.
[Genesis] [00:29:23] [INFO] Adding <gs.RigidEntity>. idx: 1, uid: <6156ff8>, morph: <gs.morphs.URDF(file='/tmp/tmptmxmqmxz.urdf')>, material: <gs.materials.Rigid>.


[Genesis] [00:29:29] [INFO] Falling back to legacy URDF parser. Default values of physics properties may be off.
[Genesis] [00:29:29] [INFO] Applying offset to base link's pose with user provided value in morph.
[Genesis] [00:29:43] [INFO] Building scene <4cb4c04>...
[Genesis] [00:30:40] [INFO] Compiling simulation kernels...
[Genesis] [00:32:58] [INFO] Building visualizer...
[Genesis] [00:32:59] [INFO] Software rendering context detected. Shadows and plane reflection not supported. Beware rendering will be extremely slow.
ERobot: measured, 6 joints (RRRRRR), dynamics, geometry, collision
┌──────┬──────────────────┬───────┬──────────────────┬─────────────────────────────────────────────────────────────────────────────┐
│ link │       link       │ joint │      parent      │                             ETS: parent to link                             │
├──────┼──────────────────┼───────┼──────────────────┼─────────────────────────────────────────────────────────────────────────────┤
│    

In [5]:
FPS = 60
dt = 1 / FPS
scene = gs.Scene(
    viewer_options=gs.options.ViewerOptions(
        camera_pos=(1.5, 1.0, 1.5),
        camera_lookat=(0, 0, 0.5),
        camera_fov=40,
        max_FPS=FPS,
    ),
    sim_options=gs.options.SimOptions(
        gravity=(0, 0, 0),
    ),
    renderer = gs.renderers.Rasterizer(), # using rasterizer for camera rendering
    show_viewer=True,
    show_FPS=False,
)

plane = scene.add_entity(
    gs.morphs.Plane(),
)
robot = scene.add_entity(
    manny.visualizer.morph,
)

[Genesis] [03:37:40] [INFO] Scene <5710cd2> created.
[Genesis] [03:37:40] [INFO] Adding <gs.RigidEntity>. idx: 0, uid: <668696e>, morph: <gs.morphs.Plane>, material: <gs.materials.Rigid>.
[Genesis] [03:37:40] [INFO] Adding <gs.RigidEntity>. idx: 1, uid: <a9764ac>, morph: <gs.morphs.URDF(file='/workspace/robots/robot.urdf')>, material: <gs.materials.Rigid>.


In [6]:
# import os
# os.environ["DISPLAY"] = ":0"
# os.environ["EGL_DEVICE_ID"] = "1"
scene.build(compile_kernels=False)

[Genesis] [03:37:42] [INFO] Building scene <5710cd2>...
[Genesis] [03:37:59] [INFO] Building visualizer...
[Genesis] [03:38:00] [INFO] Viewer created. Resolution: 720×540, max_FPS: 60.


In [11]:
for i in range(240):
    scene.step()
    scene.viewer.set_camera_pose(
        pos    = (3.0 * np.sin(i / 60), 3.0 * np.cos(i / 60), 1.5),
        lookat = (0, 0, 0.5),
    )

In [3]:
scene = manny.visualizer.scene
camera = manny.visualizer.camera

In [51]:
camera.set_pose(pos=[1.5, 2.5, 0.5], lookat=[0, 0, 0.5])
frame = camera.render()[0]
# frame.shape

image = hv.RGB(frame, bounds=(0, 0, frame.shape[1], frame.shape[0]))
image.opts(aspect=frame.shape[1] / frame.shape[0])

:RGB   [x,y]   (R,G,B)

In [ ]:
camera.start_recording()

for i in range(240):
    camera.render()
    scene.step()
    camera.set_pose(
        pos    = (3.0 * np.sin(i / 60), 3.0 * np.cos(i / 60), 1.5),
        lookat = (0, 0, 0.5),
    )

camera.stop_recording('video.mp4', fps=60)